# Práctica IDS con Suricata (ejecución remota en Jupyter)

En esta práctica aprenderás a **instalar, configurar y ejecutar Suricata** como motor IDS para:
- **Captura en vivo** (tráfico de una interfaz).
- **Análisis offline** de ficheros **PCAP**.
- **Inspección de logs** (`fast.log` y `eve.json`) para interpretar alertas y eventos.

> **Importante:** ejecuta las celdas **en orden**. Si una celda queda marcada como “opcional”, puedes saltarla si tu entorno no lo permite.


## Introducción: Suricata y los IDS

**Suricata** es un motor IDS/IPS de código abierto y alto rendimiento. Permite:
- Inspección profunda de paquetes (DPI) en tiempo real.
- Detección por firmas (reglas) y generación de alertas.
- Registro estructurado de eventos (por ejemplo en `eve.json`).

Un **IDS (Intrusion Detection System)** analiza tráfico o eventos para detectar actividad maliciosa o no autorizada. En esta práctica nos centramos en **detección y análisis**, interpretando las alertas que produce Suricata.


## Requisitos y recomendaciones

**Entorno recomendado**
- Linux (Ubuntu/Debian) con permisos de `sudo`.
- Conexión a Internet para instalar paquetes y descargar PCAPs.

**Antes de empezar**
- Si estás en un entorno gestionado (p. ej., un servidor remoto o una VM), asegúrate de tener:
  - Acceso a `sudo`.
  - Espacio libre suficiente (varios cientos de MB para reglas y PCAPs).
  - Permiso para capturar tráfico (solo necesario para el modo en vivo).

**Convención de rutas en esta práctica**
- Configuración principal: `/etc/suricata/suricata.yaml`
- Reglas actualizadas (habitual tras `suricata-update`): `/var/lib/suricata/rules/suricata.rules`
- Logs típicos: `/var/log/suricata/` (aunque puede variar si se usa `-l` al ejecutar Suricata)


# Práctica IDS – Suricata

Sigue los pasos en orden. Cuando veas un bloque con comandos, ejecútalo y revisa la salida antes de continuar.

In [ ]:
!sudo apt-get update
!sudo apt-get install -y suricata

## 1. Captura de tráfico en vivo (opcional)

En este apartado ejecutarás Suricata escuchando una **interfaz de red** y generando logs en tiempo real.

1) Lista las interfaces disponibles y elige la que corresponda a tu conexión (por ejemplo `eth0`, `enp0s3`, `wlan0`).  
2) Ejecuta Suricata en modo captura sobre esa interfaz.

> Si tu entorno **no permite captura en vivo** (p. ej., restricciones de contenedor o permisos), pasa al apartado **Análisis de PCAP**.


In [ ]:
# Ejecuta este comando para listar tus interfaces de red y encontrar el nombre de la interfaz que deseas monitorear (por ejemplo, eth0, enp0s3, wlan0).
!ip a

1: lo: <LOOPBACK,UP,LOWER_UP> mtu 65536 qdisc noqueue state UNKNOWN group default qlen 1000
    link/loopback 00:00:00:00:00:00 brd 00:00:00:00:00:00
    inet 127.0.0.1/8 scope host lo
       valid_lft forever preferred_lft forever
    inet6 ::1/128 scope host 
       valid_lft forever preferred_lft forever
7: eth0@if8: <BROADCAST,MULTICAST,UP,LOWER_UP> mtu 1500 qdisc noqueue state UP group default 
    link/ether 02:42:ac:1c:00:0c brd ff:ff:ff:ff:ff:ff link-netnsid 0
    inet 172.28.0.12/16 brd 172.28.255.255 scope global eth0
       valid_lft forever preferred_lft forever


Una vez que tengas el nombre de la interfaz (por ejemplo, `eth0`), inicia Suricata en modo captura.

- Este comando suele ejecutarse en primer plano.
- Para detenerlo, usa `Ctrl+C`.

> **Sugerencia:** si quieres ver rápidamente si se están generando alertas, revisa después los logs (`/var/log/suricata/fast.log` y `/var/log/suricata/eve.json`).


In [ ]:
# Reemplaza '<nombre_de_interfaz>' con tu interfaz real (e.g., eth0, enp0s3).
# Este comando requiere permisos de superusuario.
# !sudo suricata -i <nombre_de_interfaz> -c /etc/suricata/suricata.yaml -s /etc/suricata/rules/suricata.rules

# Ejemplo (descomenta y adapta si conoces tu interfaz):
#!sudo suricata -i eth0 -c /etc/suricata/suricata.yaml -s /etc/suricata/rules/suricata.rules

## 2. Revisar la configuración de Suricata (`suricata.yaml`)

Antes de analizar tráfico, revisaremos el fichero de configuración para entender:
- Dónde busca Suricata las **reglas**.
- Cómo están definidas las variables de red (`HOME_NET`, `EXTERNAL_NET`).
- Qué **salidas de log** están habilitadas (especialmente `fast.log` y `eve.json`).


In [ ]:
print('Contenido de /etc/suricata/suricata.yaml:')
!sudo cat /etc/suricata/suricata.yaml

Contenido de /etc/suricata/suricata.yaml:
%YAML 1.1
---

# Suricata configuration file. In addition to the comments describing all
# options in this file, full documentation can be found at:
# https://suricata.readthedocs.io/en/latest/configuration/suricata-yaml.html

##
## Step 1: Inform Suricata about your network
##

vars:
  # more specific is better for alert accuracy and performance
  address-groups:
    HOME_NET: "[192.168.0.0/16,10.0.0.0/8,172.16.0.0/12]"
    #HOME_NET: "[192.168.0.0/16]"
    #HOME_NET: "[10.0.0.0/8]"
    #HOME_NET: "[172.16.0.0/12]"
    #HOME_NET: "any"

    EXTERNAL_NET: "!$HOME_NET"
    #EXTERNAL_NET: "any"

    HTTP_SERVERS: "$HOME_NET"
    SMTP_SERVERS: "$HOME_NET"
    SQL_SERVERS: "$HOME_NET"
    DNS_SERVERS: "$HOME_NET"
    TELNET_SERVERS: "$HOME_NET"
    AIM_SERVERS: "$EXTERNAL_NET"
    DC_SERVERS: "$HOME_NET"
    DNP3_SERVER: "$HOME_NET"
    DNP3_CLIENT: "$HOME_NET"
    MODBUS_CLIENT: "$HOME_NET"
    MODBUS_SERVER: "$HOME_NET"
    ENIP_CLIENT: "$HOME_NE

## 3. Puntos clave en `suricata.yaml` (guía rápida)

En la práctica nos fijaremos especialmente en:
- **Ruta de reglas** (`default-rule-path` y `rule-files`)
- **Variables de red** (`HOME_NET`, `EXTERNAL_NET`)
- **Grupos de puertos** (`port-groups`)
- **Logs de salida** (`outputs`: `eve.json`, `fast.log`)

A continuación tienes una explicación ampliada para ayudarte a interpretar la configuración:

 de Atributos Importantes en `suricata.yaml`

El archivo `suricata.yaml` es el corazón de la configuración de Suricata. A continuación, se explican algunos de los atributos clave, con énfasis en el fichero de reglas, direcciones IP, puertos, `HOME_NET` y `EXTERNAL_NET`.

### 1. `default-rule-path`

*   **Ubicación:** Generalmente se encuentra bajo la sección `rules:`. Establece la ruta base donde Suricata buscará los archivos de reglas.
*   **Ejemplo:** `default-rule-path: /etc/suricata/rules`
*   **Importancia:** Define el directorio principal para tus reglas. `suricata-update` suele poner las reglas compiladas en `/var/lib/suricata/rules/`.

### 2. `rule-files`

*   **Ubicación:** También bajo la sección `rules:`, especifica qué archivos de reglas individuales debe cargar Suricata.
*   **Ejemplo:**
    ```yaml
    rule-files:
      - suricata.rules
      # - app-layer-events.rules
    ```
*   **Importancia:** Aquí es donde le dices a Suricata qué colecciones de reglas usar. Como se vio anteriormente, si `suricata-update` coloca las reglas en `/var/lib/suricata/rules/suricata.rules`, es crucial que esta sección apunte a esa ubicación o que el archivo `suricata.rules` en `/etc/suricata/rules/` contenga una referencia correcta.

### 3. Configuración de Red: `HOME_NET` y `EXTERNAL_NET`

Estos son dos de los parámetros más críticos en Suricata, ya que definen qué se considera tu red interna (protegida) y qué es externo a ella. Las reglas de Suricata a menudo utilizan estas variables para distinguir entre tráfico interno y externo, lo que es fundamental para la detección precisa.

*   **`HOME_NET`**
    *   **Ubicación:** Bajo la sección `vars:`. Define el rango de direcciones IP de tu red interna o la red que deseas proteger.
    *   **Ejemplo:** `HOME_NET: "[192.168.0.0/16,10.0.0.0/8,172.16.0.0/12]"`
    *   **Importancia:** Todas las direcciones IP que se encuentran dentro de este rango son consideradas 'locales' o 'internas'. Las reglas de Suricata interpretan esto para distinguir los ataques que vienen de fuera (externos a internos) de los internos (internos a internos o internos a externos).

*   **`EXTERNAL_NET`**
    *   **Ubicación:** Bajo la sección `vars:`. Define todas las direcciones IP que no son parte de `HOME_NET` (generalmente, Internet o cualquier otra red fuera de tu control).
    *   **Ejemplo:** `EXTERNAL_NET: "!$HOME_NET"`
    *   **Importancia:** `!$HOME_NET` es la forma más común y segura de configurarlo, lo que significa "todo lo que NO está en HOME_NET". Esto asegura que todo el tráfico que no es interno sea considerado externo, simplificando la escritura y el mantenimiento de las reglas.

### 4. `port-groups`

*   **Ubicación:** Bajo la sección `vars:`. Permite definir grupos de puertos comúnmente utilizados para diferentes servicios.
*   **Ejemplo:**
    ```yaml
    vars:
      # port groups
      HTTP_PORTS: "80,8080,8000,8008,8888,8443,443"
      FILE_DATA_PORTS: "$HTTP_PORTS,110,143,443,465,993,995,20,21,25,3306,5432,5900,8000,8080,8443,8888"
    ```
*   **Importancia:** Estas variables se utilizan en las reglas para que no tengas que enumerar todos los puertos en cada regla, haciendo las reglas más legibles y fáciles de mantener. Por ejemplo, una regla para tráfico HTTP puede simplemente usar `$HTTP_PORTS` en lugar de `80,8080,...`.

### 5. `outputs` (Salidas de Logs)

*   **Ubicación:** Una sección principal en el archivo `suricata.yaml`.
*   **Ejemplo (relevante):**
    ```yaml
    outputs:
      - eve-log:
          enabled: yes
          filetype: regular #regular|syslog|unix_dgram|unix_stream
          filename: eve.json
          # Appending to an existing file can be done by setting 'append' to 'yes'.
          # append: no
          # If you want to dump alerts to a separate file, you can do this:
          # - alert:
          #     enabled: yes
          #     # filetype: regular # regular|syslog|unix_dgram|unix_stream
          #     # filename: alerts.json
          #     # append: yes
      - fast.log:
          enabled: yes
          filetype: regular
          # By default, messages are appended to fast.log.
          # Change to 'no' to overwrite at startup.
          # append: yes
          filename: fast.log
          # The fast log format: tag, timestamp, alert info
          # If you want to specify a specific format for the fast log, you can use:
          # format: "%T.%{usec} %F %{%H:%M:%S} %{%Y-%m-%d} %i %s %p %d %H %M %{alert.signature} %{alert.gid} %{alert.rev} %{alert.signature_id} %{event_type} %{src_ip} %{dest_ip} %{src_port} %{dest_port} %{proto}"
    ```
*   **Importancia:** Esta sección configura dónde y cómo Suricata guarda sus logs. Hemos configurado `eve.json` para eventos detallados (incluidas alertas) y `fast.log` para alertas concisas. La ruta donde se escriben estos archivos de log puede ser sobrescrita con la opción `-l` al ejecutar Suricata (como hicimos con `/tmp/suricata_logs`).

Comprender y ajustar estas configuraciones es fundamental para un monitoreo de red eficaz con Suricata.

## 4. Análisis de ficheros PCAP

Ahora ejecutaremos Suricata en modo **offline** para analizar un PCAP ya capturado.

- Este modo es ideal para prácticas remotas, porque no requiere capturar tráfico en vivo.
- Tras el análisis, revisaremos los logs para identificar alertas y eventos relevantes.


In [ ]:
# Reemplaza '<ruta_al_archivo_pcap>' con la ruta a tu archivo PCAP.
# Este comando requiere permisos de superusuario.
# !sudo suricata -r <ruta_al_archivo_pcap> -c /etc/suricata/suricata.yaml -s /etc/suricata/rules/suricata.rules

# Ejemplo (descomenta y adapta si tienes un archivo PCAP):
# !sudo suricata -r /home/user/mi_captura.pcap -c /etc/suricata/suricata.yaml -s /etc/suricata/rules/suricata.rules

## 5. Visualización de logs de Suricata

Suricata suele generar, como mínimo, dos ficheros útiles:

- `fast.log`: listado **resumido** de alertas (rápido de inspeccionar).
- `eve.json`: eventos en **JSON** (más detallado; útil para búsquedas, filtrado y parsing).

En las siguientes celdas mostraremos ambos.
> Si los ficheros no aparecen en el directorio actual, revisa también `/var/log/suricata/`.


In [ ]:
# Muestra el contenido del log fast.log
!sudo cat /var/log/suricata/fast.log

cat: /var/log/suricata/fast.log: No such file or directory


In [ ]:
# Muestra las últimas líneas del log eve.json en tiempo real (requiere que Suricata esté corriendo y generando logs)
!sudo cat /var/log/suricata/eve.json

cat: /var/log/suricata/eve.json: No such file or directory


## 6. Descarga y descompresión de un PCAP de ejemplo

Vamos a descargar un PCAP comprimido con contraseña (caso real publicado para análisis).
- Descarga el `.zip`
- Descomprímelo con la contraseña indicada
- Verifica que el `.pcap` se ha extraído correctamente


## 7. Actualización de reglas

Antes de analizar tráfico, actualizamos las reglas para maximizar la capacidad de detección.

- `suricata-update` descarga y compila reglas en una ruta que suele ser:  
  `/var/lib/suricata/rules/suricata.rules`

> Si Suricata no encuentra reglas o muestra avisos de rutas, revisa el apartado de configuración de reglas en `suricata.yaml`.


In [ ]:
!sudo suricata-update

/usr/lib/python3/dist-packages/suricata/update/main.py:654: SyntaxWarning: invalid escape sequence '\s'
  re.compile("\s+(re:\"(.*)\")"),
/usr/lib/python3/dist-packages/suricata/update/main.py:655: SyntaxWarning: invalid escape sequence '\s'
  re.compile("\s+(re:(.*?)),.*"),
/usr/lib/python3/dist-packages/suricata/update/main.py:656: SyntaxWarning: invalid escape sequence '\s'
  re.compile("\s+(re:(.*))"),
/usr/lib/python3/dist-packages/suricata/update/main.py:1123: SyntaxWarning: invalid escape sequence '\.'
  m = re.match("app-layer\.protocols\.([^\.]+)\.enabled", key)
/usr/lib/python3/dist-packages/suricata/update/engine.py:138: SyntaxWarning: invalid escape sequence '\d'
  m = re.search("((\d+)\.(\d+)(\.(\d+))?([\w\-]+)?)", str(buf).strip())
/usr/lib/python3/dist-packages/suricata/update/osinfo.py:30: SyntaxWarning: invalid escape sequence '\w'
  m = re.match("^(\w+)=\"?(.*?)\"?$", line)
/usr/lib/python3/dist-packages/suricata/update/rule.py:439: SyntaxWarning: invalid escape seque

In [ ]:
# Descargar el archivo .pcap.zip
!wget https://www.malware-traffic-analysis.net/2024/11/24/2024-11-24-webserver-scans-and-probes.pcap.zip

# Descomprimir el archivo para obtener el .pcap con la contraseña
!unzip -P infected_20241124 2024-11-24-webserver-scans-and-probes.pcap.zip

# Listar los archivos para confirmar que el .pcap fue extraído
!ls -l

--2026-02-25 15:15:53--  https://www.malware-traffic-analysis.net/2024/11/24/2024-11-24-webserver-scans-and-probes.pcap.zip
Resolving www.malware-traffic-analysis.net (www.malware-traffic-analysis.net)... 199.201.110.204
Connecting to www.malware-traffic-analysis.net (www.malware-traffic-analysis.net)|199.201.110.204|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1555335 (1.5M) [application/zip]
Saving to: ‘2024-11-24-webserver-scans-and-probes.pcap.zip’

2024-11-24-webserve 100%[===================>]   1.48M  7.06MB/s    in 0.2s    

2026-02-25 15:15:54 (7.06 MB/s) - ‘2024-11-24-webserver-scans-and-probes.pcap.zip’ saved [1555335/1555335]

Archive:  2024-11-24-webserver-scans-and-probes.pcap.zip
  inflating: 2024-11-24-webserver-scans-and-probes.pcap  
total 5976
-rw-rw-r-- 1 root root 4556830 Nov 25  2024 2024-11-24-webserver-scans-and-probes.pcap
-rw-r--r-- 1 root root 1555335 Nov 25  2024 2024-11-24-webserver-scans-and-probes.pcap.zip
drwxr-xr-x 1 root ro

In [ ]:
import subprocess

# Backup the original suricata.yaml before modifying
!sudo cp /etc/suricata/suricata.yaml /etc/suricata/suricata.yaml.bak

# Use sed to replace the default rule path with the updated one
# This command assumes the default rule is specified as '- suricata.rules'
# and it's within the rules directory specified by 'default-rule-path'
# which is usually '/etc/suricata/rules/'.
# We'll replace the line that points to the old rules file with the new one.

# First, identify the line to replace. It's usually a line like '- suricata.rules'
# under a 'rule-files:' section.
# The suricata-update tool creates a single 'suricata.rules' in /var/lib/suricata/rules/
# So, we need to comment out any existing rule files and add the new one.

# Read the original file content
with open('/etc/suricata/suricata.yaml', 'r') as f:
    lines = f.readlines()

new_lines = []
rule_files_section = False
inserted_new_rule = False

for line in lines:
    if 'rule-files:' in line:
        new_lines.append(line) # Keep the 'rule-files:' line
        rule_files_section = True
        # Add the updated rules path immediately after the 'rule-files:' declaration
        indent = len(line) - len(line.lstrip()) # Preserve indentation
        new_lines.append(f'{' ' * indent}- /var/lib/suricata/rules/suricata.rules\n')
        inserted_new_rule = True
    elif rule_files_section and line.strip().startswith('- '):
        # Comment out old rule file entries if they are in the default path
        if '/etc/suricata/rules/' in line or 'suricata.rules' in line:
            new_lines.append(f'# {line}')
        else:
            new_lines.append(line) # Keep other rule files that might be valid
    elif rule_files_section and not line.strip(): # End of rule-files section (empty line)
        rule_files_section = False
        new_lines.append(line)
    else:
        new_lines.append(line)

# If rule-files section was not found but we need to add the rule
if not inserted_new_rule:
    # This case might be more complex if 'rule-files' section doesn't exist at all or is structured differently.
    # For this specific fix, assume 'rule-files' exists and we are modifying it.
    # If it didn't exist, we would need to insert it strategically.
    # For simplicity, if not found and not inserted, we assume it's already handled or not relevant.
    # In a real scenario, more robust parsing might be needed.
    pass # No action needed if rule was inserted correctly above or no rule-files section to begin with

# Write the modified content back to suricata.yaml
with open('/etc/suricata/suricata.yaml', 'w') as f:
    f.writelines(new_lines)

print("suricata.yaml updated to use rules from /var/lib/suricata/rules/suricata.rules")


suricata.yaml updated to use rules from /var/lib/suricata/rules/suricata.rules


In [ ]:
import os

pcap_file_path = '/content/2024-11-24-webserver-scans-and-probes.pcap'
config_file_path = '/etc/suricata/suricata.yaml'
rules_file_path = '/var/lib/suricata/rules/suricata.rules' # This path is now also configured in suricata.yaml

# Ensure the PCAP file exists before trying to analyze it
if not os.path.exists(pcap_file_path):
    print(f"Error: PCAP file not found at {pcap_file_path}")
else:
    print(f"Re-analyzing PCAP file: {pcap_file_path} with updated configuration...")
    !sudo suricata -r {pcap_file_path} -c {config_file_path} --runmode autofp

# Note: We can now potentially omit the -s argument as the rules path is set in the config file,
# but keeping it explicitly here is also harmless as it overrides the config if different.
# However, to truly test the config file modification, we can remove -s. Let's remove -s
# to confirm the config file change took effect for rules loading.
# Re-executing without -s to rely solely on the updated suricata.yaml for rules path.
print("Re-analyzing PCAP file again, relying on updated suricata.yaml for rules path...")
!sudo suricata -r {pcap_file_path} -c {config_file_path} --runmode autofp

Re-analyzing PCAP file: /content/2024-11-24-webserver-scans-and-probes.pcap with updated configuration...
25/2/2026 -- 15:15:54 - <Notice> - This is Suricata version 6.0.4 RELEASE running in USER mode
25/2/2026 -- 15:17:53 - <Notice> - all 3 packet processing threads, 4 management threads initialized, engine started.
25/2/2026 -- 15:17:53 - <Notice> - Signal Received.  Stopping engine.
25/2/2026 -- 15:17:54 - <Notice> - Pcap-file module read 1 files, 54629 packets, 3682742 bytes
Re-analyzing PCAP file again, relying on updated suricata.yaml for rules path...
25/2/2026 -- 15:17:54 - <Notice> - This is Suricata version 6.0.4 RELEASE running in USER mode
25/2/2026 -- 15:19:54 - <Notice> - all 3 packet processing threads, 4 management threads initialized, engine started.
25/2/2026 -- 15:19:55 - <Notice> - Signal Received.  Stopping engine.
25/2/2026 -- 15:19:55 - <Notice> - Pcap-file module read 1 files, 54629 packets, 3682742 bytes


In [ ]:
print("Contenido de fast.log después del análisis de WannaCry:")
!sudo cat fast.log

In [ ]:
print("Contenido de eve.json después del análisis de WannaCry:")
!sudo cat eve.json

## 8. Caso de estudio: WannaCry / EternalBlue (PCAP histórico)

En este apartado analizaremos un PCAP histórico asociado al exploit **EternalBlue** (MS17-010) usado en campañas como WannaCry.

Objetivo:
- Ejecutar Suricata sobre el PCAP.
- Inspeccionar `fast.log` y `eve.json` buscando alertas relevantes.


In [ ]:
pcap_zip_url = 'https://www.malware-traffic-analysis.net/2017/05/18/2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip'
pcap_password = 'infected_20170518'

# Descargar el archivo .pcap.zip
print(f"Descargando el archivo: {pcap_zip_url}")
!wget {pcap_zip_url}

# Descomprimir el archivo para obtener el .pcap con la contraseña
pcap_zip_filename = pcap_zip_url.split('/')[-1]
print(f"Descomprimiendo el archivo: {pcap_zip_filename} con contraseña...")
!unzip -P {pcap_password} {pcap_zip_filename}

# Listar los archivos para confirmar que el .pcap fue extraído
print("Listando archivos en el directorio actual:")
!ls -l

Descargando el archivo: https://www.malware-traffic-analysis.net/2017/05/18/2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip
--2026-02-25 15:25:18--  https://www.malware-traffic-analysis.net/2017/05/18/2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip
Resolving www.malware-traffic-analysis.net (www.malware-traffic-analysis.net)... 199.201.110.204
Connecting to www.malware-traffic-analysis.net (www.malware-traffic-analysis.net)|199.201.110.204|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 23857652 (23M) [application/zip]
Saving to: ‘2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip’

2017-05-18-WannaCry 100%[===================>]  22.75M  43.3MB/s    in 0.5s    

2026-02-25 15:25:18 (43.3 MB/s) - ‘2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip’ saved [23857652/23857652]

Descomprimiendo el archivo: 2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap.zip con contraseña...
Archiv

In [ ]:
import os

pcap_file_path = '/content/2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap'
config_file_path = '/etc/suricata/suricata.yaml'
rules_file_path = '/var/lib/suricata/rules/suricata.rules' # This path is now also configured in suricata.yaml

# Ensure the PCAP file exists before trying to analyze it
if not os.path.exists(pcap_file_path):
    print(f"Error: PCAP file not found at {pcap_file_path}")
else:
    print(f"Re-analyzing PCAP file: {pcap_file_path} with updated configuration...")
    !sudo suricata -r {pcap_file_path} -c {config_file_path} --runmode autofp

# Note: We can now potentially omit the -s argument as the rules path is set in the config file,
# but keeping it explicitly here is also harmless as it overrides the config if different.
# However, to truly test the config file modification, we can remove -s. Let's remove -s
# to confirm the config file change took effect for rules loading.
# Re-executing without -s to rely solely on the updated suricata.yaml for rules path.
print("Re-analyzing PCAP file again, relying on updated suricata.yaml for rules path...")
!sudo suricata -r {pcap_file_path} -c {config_file_path} --runmode autofp

Re-analyzing PCAP file: /content/2017-05-18-WannaCry-ransomware-using-EnternalBlue-exploit.pcap with updated configuration...
25/2/2026 -- 15:25:53 - <Notice> - This is Suricata version 6.0.4 RELEASE running in USER mode
25/2/2026 -- 15:28:01 - <Notice> - all 3 packet processing threads, 4 management threads initialized, engine started.
25/2/2026 -- 15:28:02 - <Notice> - Signal Received.  Stopping engine.
25/2/2026 -- 15:28:02 - <Notice> - Pcap-file module read 1 files, 46654 packets, 37044839 bytes
Re-analyzing PCAP file again, relying on updated suricata.yaml for rules path...
25/2/2026 -- 15:28:03 - <Notice> - This is Suricata version 6.0.4 RELEASE running in USER mode
25/2/2026 -- 15:30:07 - <Notice> - all 3 packet processing threads, 4 management threads initialized, engine started.
25/2/2026 -- 15:30:07 - <Notice> - Signal Received.  Stopping engine.
25/2/2026 -- 15:30:08 - <Notice> - Pcap-file module read 1 files, 46654 packets, 37044839 bytes


In [ ]:
print("Contenido de fast.log después del análisis de WannaCry:")
!sudo cat fast.log

Se han truncado las últimas 5000 líneas del flujo de salida.
05/18/2017-08:13:59.590630  [**] [1:2024216:2] ET EXPLOIT Possible DOUBLEPULSAR Beacon Response [**] [Classification: A Network Trojan was detected] [Priority: 1] {TCP} 192.168.116.149:445 -> 192.168.116.138:2009
05/18/2017-08:13:59.591058  [**] [1:2024216:2] ET EXPLOIT Possible DOUBLEPULSAR Beacon Response [**] [Classification: A Network Trojan was detected] [Priority: 1] {TCP} 192.168.116.149:445 -> 192.168.116.138:2009
05/18/2017-08:13:41.064894  [**] [1:2024216:2] ET EXPLOIT Possible DOUBLEPULSAR Beacon Response [**] [Classification: A Network Trojan was detected] [Priority: 1] {TCP} 192.168.116.172:445 -> 192.168.116.138:1605
05/18/2017-08:13:41.066911  [**] [1:2024216:2] ET EXPLOIT Possible DOUBLEPULSAR Beacon Response [**] [Classification: A Network Trojan was detected] [Priority: 1] {TCP} 192.168.116.172:445 -> 192.168.116.138:1605
05/18/2017-08:13:41.067442  [**] [1:2024216:2] ET EXPLOIT Possible DOUBLEPULSAR Beacon 

In [ ]:
print("Contenido de eve.json después del análisis de WannaCry:")
!sudo cat eve.json

Streaming output truncated to the last 5000 lines.
{"timestamp":"2017-05-18T08:13:42.568253+0000","flow_id":51968428367596,"pcap_cnt":20705,"event_type":"alert","src_ip":"192.168.116.172","src_port":445,"dest_ip":"192.168.116.149","dest_port":52414,"proto":"TCP","metadata":{"flowbits":["smb.tree.connect.ipc"]},"alert":{"action":"allowed","gid":1,"signature_id":2024216,"rev":2,"signature":"ET EXPLOIT Possible DOUBLEPULSAR Beacon Response","category":"A Network Trojan was detected","severity":1,"metadata":{"attack_target":["Client_Endpoint"],"confidence":["Medium"],"created_at":["2017_04_17"],"deployment":["Internal","Perimeter"],"mitre_tactic_id":["TA0010"],"mitre_tactic_name":["Exfiltration"],"mitre_technique_id":["T1041"],"mitre_technique_name":["Exfiltration_Over_C2_Channel"],"signature_severity":["Major"],"tag":["c2"],"updated_at":["2019_09_28"]}},"app_proto":"smb","flow":{"pkts_toserver":744,"pkts_toclient":497,"bytes_toserver":1068437,"bytes_toclient":38353,"start":"2017-05-18T08: